In [29]:
import os,re,time,json,sys

"""
模板文件目录下 题目清单.tex 文件不能缺失
"""

"""---设置题目列表---"""
#留空为编译全题库, a为读取临时文件中的题号筛选.txt文件生成题库
problems = r"""
003589,003590,003592,003593,003597,003601,003603,003604,003605,003607,003609,003610,003612,003613,003620,003622,003624,003625,003626,003628,003631,003632,003633,003636,003637,003642,003644,003646,003647,003649,003655,003656,003658,003665,003667,003668,003669,003673,003675,003676,003677,003679,003680,003681,003683,003689,003690,003693,003694,003695,003697,003698,003699,003700,004059,004061,004066,004067,004069,004070,004072,004074,004075,004076,004079,004081,004086,004088,004089,004090,004093,004094,004096,004097,004101,004102,004112,004113,004115,004117,004118,004119,004123,004124,004126,004130,004132,004133,004135,004136,004137,004138,004139,004143,004144,004145,004149,004151,004153,004154,004155,004159,004160,004162,004165,004168,004171,004172,004174,004175,004176,004177,004185,004186,004190,004191,004194,004198,004199,004200,004201,004202,004203,004205,004206,004208,004209,004214,004215,004217,004218,004219,004220,004221,004222,004223,004227,004228,004229,004230,004233,004234,004235,004236,004238,004241,004243,004244,004249,004253,004256,004258,004259,004261,004264,004266,004269,004270,004271,004272,004273,004274,004277,004278,004279,004284,004285,004286,004287,004289,004290,004291,004292,004293,004295,004301,004302,004305,004306,004307,004308,004311,004313,004314,004315,004316,004319,004323,004325,004326,004327,004329,004332,004333,004335,004336,004337,004339,004344,004345,004347,004348,004349,004350,004353,004354,004355,004357,004358,004360,004362,004364,004365,004366,004367,004368,004369,004371,004373,004374,004375,004376,004377,004378,004379,004380,004381,004382,004383,004384,004386,004387,004388,004389,004390,004391,004392,004393,004395,004396,004397,004398,004399,004401,004403,004404,004405,004406,004407,004408,004410,004411,004413,004415,004416,004417,004418,004419,004420,004421,004422,004423,004425,004426,004427,004429,004431,004432,004433,004434,004435,004436,004437,004438,004441,004442,004443,004445,004446,004447,004448,004449,004452,004454,004455,004456,004457,004458,004460,004461,004462,004463,004464,004465,004466,004468,004469,004470,004471,004477,004479,004481,004482,004483,004484,004485,004486,004489,004490,004493,004496,004498,004499,004500,004502,004503,004505,004506,004510,004512,004515,004516,004518,004520,004522,004523,004525,004526,004527,004530,004531,004532,004533,004540,004541,004542,004543,004544,004545,004546,004547,004549,004552,004554,004555,004556,004559,004562,004563,004564,004565,004567,004569,004571,004619,004620,004621,004623,004630,004631,004634,004635,004637,004640,004641,004645,004646,004649,004650,004652,004655,004656,004657,004658,004661,004662,004664,004665,004666,004667,004668,004669,004671,004673,004674,004675,004676,004677,004679,004681,004703,004704,004706,004707,004708,004714,004715,004719,004721,004745,004754,004755,004756,004757,004759,004760,004761,004762,004763,009984,009986,009988,009991,009994,009995,009996,009997,009998,010000,010001,010002


"""
"""---设置题目列表结束---"""

"""---设置文件名---"""
#目录和文件的分隔务必用/
filename = "临时文件/test"
"""---设置文件名结束---"""



#读取系统日期
current_time = time.localtime()
time_string = "_"+str(current_time.tm_year).zfill(4)+str(current_time.tm_mon).zfill(2)+str(current_time.tm_mday).zfill(2)

teachers_latex_file = filename + "_教师用" + time_string + ".tex"
students_latex_file = filename + "_学生用" + time_string + ".tex"

#生成数码列表, 逗号分隔每个区块, 区块内部用:表示整数闭区间
def generate_number_set(string,dict):
    string = re.sub(r"[\n\s]","",string)
    string_list = string.split(",")
    numbers_list = []
    for s in string_list:
        if not ":" in s:
            numbers_list.append(s.zfill(6))
        else:
            start,end = s.split(":")
            for ind in range(int(start),int(end)+1):
                numbers_list.append(str(ind).zfill(6))
    return numbers_list

#将正确率转化为含颜色代码的字符串
def get_color(value):
    value = float(value)
    if value>=0.5:
        (r,g,b)=(1,2-2*value,0)
    else:
        (r,g,b)=(2*value,1,0)
    return "{" + "%.3f" %(r) + "," + "%.3f" %(g) + ",0}"


def color_value(matchobj):
    value = matchobj.group(1)
    return "\t"+"\\fcolorbox[rgb]{0,0,0}"+ get_color(value) +"{" + value +"}"


#读取题库json文件并转化为字典
with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)

#读取目标数据库json并转化为字典
with open(r"../题库0.3/LessonObj.json","r",encoding = "utf8") as f:
    database = f.read()
obj_dict = json.loads(database)

#生成题目列表
if problems.strip() == "":
    problem_list = list(pro_dict.keys())
elif problems.strip()[0] == "a":
    with open("文本文件/题号筛选.txt","r",encoding = "utf8") as f:
        problems = f.read()
    problem_list = [id for id in generate_number_set(problems.strip(),pro_dict) if id in pro_dict]
else:
    problem_list = [id for id in generate_number_set(problems.strip(),pro_dict) if id in pro_dict]

data_teachers = ""
data_students = ""
id_list = ""

#生成教师题目字符串与学生题目字符串, 准备替换至latex文件
for id in problem_list:
    problemset = pro_dict[id]
    problem = problemset["content"]
    solution = (problemset["solution"] if problemset["solution"] != "" else "暂无解答与提示")
    answer = "\\textcolor{red}{" + (problemset["ans"] if problemset["ans"] != "" else "暂无答案") + "}"
    remarks = (problemset["remark"] if problemset["remark"] != "" else "暂无备注")
    usages_list = problemset["usages"]
    if len(usages_list) > 0:
        usage = re.sub("\\t([\d]\.[\d]{0,10})",color_value,"\n\n".join(usages_list))
        usage = re.sub("[\\t ]([\d]\.[\d]{0,10})",color_value,usage)
    else:
        usage = "暂无使用记录"
    origin = (problemset["origin"] if problemset["origin"] != "" else "出处不详")
    objects = problemset["objs"]
    if len(objects) == 0:
        objects = "暂未关联目标\n\n"
    elif "KNONE" in [o.upper() for o in objects]:
        objects = "该题的考查目标不在目前的集合中\n\n"
    else:
        objects_string = ""
        for obj in objects:
            if not obj in obj_dict:
                objects_string = "目标" + obj + "有误\n\n"
                break
            else:
                objects_string += "\\textcolor{blue}{" + obj + "|" + obj_dict[obj]["content"] + "}\n\n"
        objects = objects_string
    space = ("" if problemset["space"] == "" else "\n"+r"\vspace*{"+problemset["space"]+"}\n")
    tags = ("|".join(problemset["tags"]) if len(problemset["origin"])>0 else "暂无标签")
    raw_string = "\\item " + "{\\tiny ("+id+")}"+problem
    teachers_string = raw_string.replace("\\tiny","")+"\n\n关联目标:\n\n"+ objects + "\n\n标签: " + tags + "\n\n答案: "+answer + "\n\n" + "解答或提示: " + solution + "\n\n使用记录:\n\n"+ usage + "\n" + "\n\n备注: " + remarks + "\n\n出处: "+origin + "\n"
    students_string = raw_string + space + "\n\n"
    data_teachers += teachers_string
    data_students += students_string



#替换latex文件的内容并编译
with open("模板文件/题目清单.tex","r",encoding = "utf8") as f:
    latex_raw = f.read()

#识别操作系统
if sys.platform != "win32":
    latex_raw = re.sub(r"fontset[\s]*=[\s]*windows","fontset = fandol",latex_raw)
    latex_raw = re.sub(r"\\setCJKmainfont",r"% \\setCJKmainfont",latex_raw)

latex_teachers = latex_raw.replace("编译模板",data_teachers)
with open(teachers_latex_file,"w",encoding = "utf8") as f:
    f.write(latex_teachers)
print("开始编译教师版本pdf文件: ", teachers_latex_file)
d = re.search("/[^/]*$",teachers_latex_file).span()[0]
pdf_dir = teachers_latex_file[:d]
os.system("xelatex -interaction=batchmode -output-directory=" + pdf_dir + " "+ teachers_latex_file)
print(os.system("xelatex -interaction=batchmode -output-directory=" + pdf_dir + " "+ teachers_latex_file))

latex_students = latex_raw.replace("编译模板",data_students)
with open(students_latex_file,"w",encoding = "utf8") as f:
    f.write(latex_students)
print("开始编译学生版本pdf文件: ", students_latex_file)
d = re.search("/[^/]*$",students_latex_file).span()[0]
pdf_dir = students_latex_file[:d]
os.system("xelatex -interaction=batchmode -output-directory=" + pdf_dir + " "+ students_latex_file)
print(os.system("xelatex -interaction=batchmode -output-directory=" + pdf_dir + " "+ students_latex_file))


开始编译教师版本pdf文件:  临时文件/test_教师用_20221025.tex
0
开始编译学生版本pdf文件:  临时文件/test_学生用_20221025.tex
0
